# Basic Analysis

In this notebook we load the data and do simple analysis.

In [1]:
# constants
LABELED_DATA = "../../data/raw/labeled.csv"
UNLABELED_DATA = "../../data/raw/unlabeled.csv"
OUT_DIR = "../../data/intermediate"

# imports
import pandas as pd
import re
from typing import List, Set, Dict, Tuple

## Load Data

First, we load the data and briefly inspect it.

In [2]:
labeled_df = pd.read_csv(LABELED_DATA, index_col=1, parse_dates=["Ticket_Closed", "Ticket_Opened_Date"])
labeled_df

Unnamed: 0                                   Problem_Abstract  \
Ticket                                                                     
272431733           0      The CUC Database is not running on DURPRIPT7B   
271472293           2  OPEN CR:Alerts not being generated  -  trap ba...   
256576476           3  Enhancement to TWB Portal GPS SYNC Reports - A...   
271503232           4  Duplicated/ triplicated exceptions on Exceptio...   
277339571           8     vnsd90, HPE account, JuniperRPM VitalArt issue   
...               ...                                                ...   
312147646        5889  Add new users to the Existing  Domain Name: MS...   
312152059        5890  Add new users to the Existing Domain Name: MSS...   
312229727        5894                                Need password reset   
312605830        5897  Customer needs access MSS_WOKA domain. This is...   
312812839        5899               Add Andrew Patterson  to State of TN   

          Ticket_Type                         Team  Ticket_Opened_Date  \
Ticket                                                                   
272431733        User                    Prognosis 2019-12-18 14:20:00   
271472293        User               SMARTS/GFP_CPE 2019-11-20 18:33:00   
256576476        User               INCM (Voyence) 2019-02-19 19:34:00   
271503232        User                       ATTLAS 2019-11-21 13:11:00   
277339571        User  VitalNet Problems or Errors 2020-05-08 22:38:00   
...               ...                          ...                 ...   
312147646        User                 GTAC - Other 2022-07-29 17:39:00   
312152059        User                 GTAC - Other 2022-07-29 20:34:00   
312229727        User  VitalNet Problems or Errors 2022-08-02 16:42:00   
312605830        User                         GTAC 2022-08-16 19:08:00   
312812839        User               ADDTAC - Other 2022-08-24 18:56:00   

                Ticket_Closed  
Ticket                         
272431733 2022-07-27 20:49:00  
271472293 2021-12-23 10:44:00  
256576476 2022-08-12 16:35:00  
271503232 2021-11-07 11:22:00  
277339571 2021-12-23 10:44:00  
...                       ...  
312147646 2022-08-02 19:13:00  
312152059 2022-08-01 16:11:00  
312229727 2022-08-02 21:33:00  
312605830 2022-08-24 14:38:00  
312812839 2022-08-31 16:00:00  

[4741 rows x 6 columns]

In [3]:
labeled_df["Ticket_Type"].value_counts()

User    4741
Name: Ticket_Type, dtype: int64

In [4]:
labeled_df.drop(columns=["Ticket_Type", "Unnamed: 0"], inplace=True)
labeled_df.rename(columns=lambda s: s.lower(), inplace=True)
labeled_df.index.rename("ticket", inplace=True)
labeled_df = labeled_df.reset_index()
labeled_df

ticket                                   problem_abstract  \
0     272431733      The CUC Database is not running on DURPRIPT7B   
1     271472293  OPEN CR:Alerts not being generated  -  trap ba...   
2     256576476  Enhancement to TWB Portal GPS SYNC Reports - A...   
3     271503232  Duplicated/ triplicated exceptions on Exceptio...   
4     277339571     vnsd90, HPE account, JuniperRPM VitalArt issue   
...         ...                                                ...   
4736  312147646  Add new users to the Existing  Domain Name: MS...   
4737  312152059  Add new users to the Existing Domain Name: MSS...   
4738  312229727                                Need password reset   
4739  312605830  Customer needs access MSS_WOKA domain. This is...   
4740  312812839               Add Andrew Patterson  to State of TN   

                             team  ticket_opened_date       ticket_closed  
0                       Prognosis 2019-12-18 14:20:00 2022-07-27 20:49:00  
1                  SMARTS/GFP_CPE 2019-11-20 18:33:00 2021-12-23 10:44:00  
2                  INCM (Voyence) 2019-02-19 19:34:00 2022-08-12 16:35:00  
3                          ATTLAS 2019-11-21 13:11:00 2021-11-07 11:22:00  
4     VitalNet Problems or Errors 2020-05-08 22:38:00 2021-12-23 10:44:00  
...                           ...                 ...                 ...  
4736                 GTAC - Other 2022-07-29 17:39:00 2022-08-02 19:13:00  
4737                 GTAC - Other 2022-07-29 20:34:00 2022-08-01 16:11:00  
4738  VitalNet Problems or Errors 2022-08-02 16:42:00 2022-08-02 21:33:00  
4739                         GTAC 2022-08-16 19:08:00 2022-08-24 14:38:00  
4740               ADDTAC - Other 2022-08-24 18:56:00 2022-08-31 16:00:00  

[4741 rows x 5 columns]

In [5]:
unlabeled_df = pd.read_csv(UNLABELED_DATA, index_col=0)
unlabeled_df

Problem_Abstract  Unnamed: 2  \
Ticket                                                                     
306416331                          BLMO ALRMS - TOUR'S START         NaN   
306423610  V211200276 & V211200279 CFB: Cheez-It Bowl: Cl...         NaN   
306428596                            BLMO ALRMS - TOUR'S END         NaN   
306428597                                  DAILY T/U  - 13 -         NaN   
306435661                               Reference V220100002         NaN   
...                                                      ...         ...   
308315612     HBO GAME THEORY EP1 - TEST 3/10/22 1730 - 1845         NaN   
308315606   DOME STARS@CANADIENS 3/17/22 1300 - 3/18/22 0100         NaN   
308315599           THE MASTER WF 4/5/22 0001 - 4/12/11 2359         NaN   
308315266  Getting error when Creating CR/SRs in serviceN...         NaN   
308313822  xxxxxxx/ccakey/ URL is no longer working--403 ...         NaN   

           Unnamed: 3  
Ticket                 
306416331         NaN  
306423610         NaN  
306428596         NaN  
306428597         NaN  
306435661         NaN  
...               ...  
308315612         NaN  
308315606         NaN  
308315599         NaN  
308315266         NaN  
308313822         NaN  

[19402 rows x 3 columns]

In [6]:
unlabeled_df.drop(columns=["Unnamed: 2", "Unnamed: 3"], inplace=True)
unlabeled_df.rename(columns={"Problem_Abstract": "problem_abstract"}, inplace=True)
unlabeled_df.index.rename("ticket", inplace=True)
unlabeled_df = unlabeled_df.reset_index()
unlabeled_df

ticket                                   problem_abstract
0      306416331                          BLMO ALRMS - TOUR'S START
1      306423610  V211200276 & V211200279 CFB: Cheez-It Bowl: Cl...
2      306428596                            BLMO ALRMS - TOUR'S END
3      306428597                                  DAILY T/U  - 13 -
4      306435661                               Reference V220100002
...          ...                                                ...
19397  308315612     HBO GAME THEORY EP1 - TEST 3/10/22 1730 - 1845
19398  308315606   DOME STARS@CANADIENS 3/17/22 1300 - 3/18/22 0100
19399  308315599           THE MASTER WF 4/5/22 0001 - 4/12/11 2359
19400  308315266  Getting error when Creating CR/SRs in serviceN...
19401  308313822  xxxxxxx/ccakey/ URL is no longer working--403 ...

[19402 rows x 2 columns]

## Clean Labels

We deal with unification of teams and removing bad open/close timestamps.

### Time

In [7]:
labeled_df["ticket_opened_date"].isna().sum()

0

In [8]:
labeled_df["ticket_closed"].isna().sum()

1

In [9]:
(labeled_df["ticket_opened_date"] > labeled_df["ticket_closed"]).sum()

0

In [10]:
def clean_time(df: pd.DataFrame) -> pd.DataFrame:

    # drop rows when time is not available
    df = df.copy().dropna(how="any", subset=["ticket_opened_date", "ticket_closed"])
    
    # calculate time
    time_to_resolve = df["ticket_closed"] - df["ticket_opened_date"]
    seconds_to_resolve = time_to_resolve.dt.total_seconds()
    df["hours_to_resolve"] = (seconds_to_resolve / 3600).apply(int)

    # drop old ones
    df.drop(columns=["ticket_opened_date", "ticket_closed"], inplace=True)
    return df

labeled_df = clean_time(labeled_df)
labeled_df

ticket                                   problem_abstract  \
0     272431733      The CUC Database is not running on DURPRIPT7B   
1     271472293  OPEN CR:Alerts not being generated  -  trap ba...   
2     256576476  Enhancement to TWB Portal GPS SYNC Reports - A...   
3     271503232  Duplicated/ triplicated exceptions on Exceptio...   
4     277339571     vnsd90, HPE account, JuniperRPM VitalArt issue   
...         ...                                                ...   
4736  312147646  Add new users to the Existing  Domain Name: MS...   
4737  312152059  Add new users to the Existing Domain Name: MSS...   
4738  312229727                                Need password reset   
4739  312605830  Customer needs access MSS_WOKA domain. This is...   
4740  312812839               Add Andrew Patterson  to State of TN   

                             team  hours_to_resolve  
0                       Prognosis             22854  
1                  SMARTS/GFP_CPE             18328  
2                  INCM (Voyence)             30477  
3                          ATTLAS             17206  
4     VitalNet Problems or Errors             14244  
...                           ...               ...  
4736                 GTAC - Other                97  
4737                 GTAC - Other                67  
4738  VitalNet Problems or Errors                 4  
4739                         GTAC               187  
4740               ADDTAC - Other               165  

[4740 rows x 4 columns]

### Team

In [11]:
labeled_df["team"].unique()

array(['Prognosis', 'SMARTS/GFP_CPE', 'INCM (Voyence)', 'ATTLAS',
       'VitalNet Problems or Errors', 'NETBRAIN - Other', 'GTAC - Other',
       'GTAC - Audit or GTAC report data', 'GTAC', 'NETBRAIN',
       'GTAC - Account issues, password change',
       'TRUE (Ticket Rules Update Engine)', 'ACTION Suite - Other',
       'NagiosXI', 'Fingertip', 'iGEMS CoE', 'ACAT', 'ADDTAC - Other',
       'Global Password Changes', 'Netbrain',
       'Customer Advocacy and IS&NS Reporting', 'Global Delivery',
       'Service Assurance Data', 'Global Delivery Data & Analytics',
       'Customer Advocacy, SI&NS and Cybersecurity Data & Analytics',
       'ADDTAC - Problem Management (ADDTAC Problem) ', 'B2B VPN Viewer',
       'cback', 'GESS SDWAN Support - Other', 'Express Ticketing',
       'Cisco ISE', 'Cisco ISE - Other', 'INCM (Voyence) - Other', 'ART',
       'BRAIN Web Site', 'Unified Task Management System (UTMS)', 'ASHE',
       'ACTION Config Audits',
       'CISCO ISE - Network Device Up

In [12]:
counts = (labeled_df["team"].value_counts() == 1)
counts[counts].index

Index(['ADDTAC', 'BizOps Database Shared Services', 'On-Demand RA Reports',
       'MDB Post-It', 'global outage | UD', 'FirstNet', 'iGems Orchestrator',
       'SD-SMART', 'iNote', 'ExpressTicketing (Internal)', 'Aruba ClearPass',
       'Pandora's Box', 'GTAC - related to 305184666', 'UTM master ticket',
       'GTAC - Logs and GTLV View', 'GTAC | pending cust/T3 response',
       'Knowledgebase Portal - M5 Apps and Tools', 'ACTION Suite',
       'Task Manager', 'Dev to check refresh of the table.',
       'Service Assurance Data', 'Action report',
       'Ticketing Gateway Interface (TGIF)',
       'GTAC - MSS acc creation, pending nw owner approval/ticket',
       'No tic cut', 'iGEMS-NG (NextGEMS) - New Customer',
       'RCAP / Circ.issue /ENO 308437459 ',
       'SWOT (Single Web Ordering Tool) Back End API'],
      dtype='object')

In [13]:
counts = (labeled_df["team"].value_counts() == 2)
counts[counts].index

Index(['iGEMS-NG (NextGEMS) - Other',
       'GESS SDWAN Support - Customer Onboarding', 'LCM Tracker', 'ART',
       'TFTP Boot', 'Prognosis', 'Netbrain', 'Security Audits'],
      dtype='object')

In [14]:
counts = (labeled_df["team"].value_counts() == 3)
counts[counts].index

Index(['Barcode Asset Scan and Ship (BASS)', 'B2B VPN Viewer'], dtype='object')

In [15]:
def unify_team(label: str, and_mapping: List[Tuple[List[str], str]], token_unifiers: List[str]) -> str:

  label = label.lower()
  # check and mapping in label
  for and_from, to in and_mapping:
    if all((a in label for a in and_from)):
      return to

  # if there is token unifier present, then return it
  tokens = set(re.split("\s+|-|,", label))
  for unifier in token_unifiers:
    if unifier in tokens:
      return unifier
  
  # otherwise just return the already used label
  return label


def clean_team(df: pd.DataFrame,
              labels_to_drop: List[str]=[
                    "application response slow or application unreachable",
                    "dev to check refresh of the table.",
                    "help using application (e.g. config pull/update, ios upgrade, etc.)"
                  ],
              and_mapping: List[Tuple[List[str], str]]=[ #
                (["express", "ticketing"], "express ticketing"),
                (["servicenow"], "service")
              ],
              token_unifiers: List[str]=[ # if such token appears then unify it around it
                "acs", "action", "addtac", "cisco", "advocacy", "global", 
                "gtac", "incm", "netbrain", "igems", 
                "security", "unified", "service", "gess"
              ],
              other_threshold: int=5,
              other_label="OTHER"
              ) -> pd.DataFrame:

  df = df.dropna(how="any", subset=["team"])
  # drop some teams
  df = df[~(df["team"].isin(labels_to_drop))]
  # unify teams
  df["team"] = df["team"].apply(lambda t: unify_team(t, and_mapping, token_unifiers))
  # group teams below threshold
  other_teams = set([
    team 
    for team, count 
    in labeled_df["team"].value_counts().to_dict().items() 
    if count < other_threshold
    ])
  df["team"] = df["team"].apply(lambda t: other_label if t in other_teams else t)
  return df

labeled_df = clean_team(labeled_df)
labeled_df

ticket                                   problem_abstract  \
0     272431733      The CUC Database is not running on DURPRIPT7B   
1     271472293  OPEN CR:Alerts not being generated  -  trap ba...   
2     256576476  Enhancement to TWB Portal GPS SYNC Reports - A...   
3     271503232  Duplicated/ triplicated exceptions on Exceptio...   
4     277339571     vnsd90, HPE account, JuniperRPM VitalArt issue   
...         ...                                                ...   
4736  312147646  Add new users to the Existing  Domain Name: MS...   
4737  312152059  Add new users to the Existing Domain Name: MSS...   
4738  312229727                                Need password reset   
4739  312605830  Customer needs access MSS_WOKA domain. This is...   
4740  312812839               Add Andrew Patterson  to State of TN   

                             team  hours_to_resolve  
0                       prognosis             22854  
1                  smarts/gfp_cpe             18328  
2                            incm             30477  
3                          attlas             17206  
4     vitalnet problems or errors             14244  
...                           ...               ...  
4736                         gtac                97  
4737                         gtac                67  
4738  vitalnet problems or errors                 4  
4739                         gtac               187  
4740                       addtac               165  

[4740 rows x 4 columns]

In [16]:
labeled_df["team"].value_counts()

gtac                                            1532
smarts/gfp_cpe                                   684
unified                                          540
cisco                                            512
global                                           247
                                                ... 
rcap / circ.issue /eno 308437459                   1
utm master ticket                                  1
on-demand ra reports                               1
sd-smart                                           1
swot (single web ordering tool) back end api       1
Name: team, Length: 63, dtype: int64

## Merge Data and Remove Duplicates

We merge the unlabeled and labeled data properly into one dataset.

In [17]:
len(list(set(labeled_df["ticket"].to_list()).intersection(unlabeled_df["ticket"].to_list())))

3073

In [18]:
def merge_dfs(labeled: pd.DataFrame, unlabeled: pd.DataFrame, id_col: str="ticket") -> pd.DataFrame:

    labeled_ids = set(labeled[id_col].to_list())
    unlabeled_new = unlabeled[unlabeled[id_col].apply(lambda id: id not in labeled_ids)].copy()
    unlabeled_new["team"] = None
    unlabeled_new["hours_to_resolve"] = None
    return labeled.append(unlabeled_new, ignore_index=True)

df = merge_dfs(labeled_df, unlabeled_df)
df

ticket                                   problem_abstract  \
0      272431733      The CUC Database is not running on DURPRIPT7B   
1      271472293  OPEN CR:Alerts not being generated  -  trap ba...   
2      256576476  Enhancement to TWB Portal GPS SYNC Reports - A...   
3      271503232  Duplicated/ triplicated exceptions on Exceptio...   
4      277339571     vnsd90, HPE account, JuniperRPM VitalArt issue   
...          ...                                                ...   
19126  308316028            HBO GAME THEORY EP1 3/13/22 1700 - 2359   
19127  308315612     HBO GAME THEORY EP1 - TEST 3/10/22 1730 - 1845   
19128  308315606   DOME STARS@CANADIENS 3/17/22 1300 - 3/18/22 0100   
19129  308315599           THE MASTER WF 4/5/22 0001 - 4/12/11 2359   
19130  308315266  Getting error when Creating CR/SRs in serviceN...   

                              team hours_to_resolve  
0                        prognosis            22854  
1                   smarts/gfp_cpe            18328  
2                             incm            30477  
3                           attlas            17206  
4      vitalnet problems or errors            14244  
...                            ...              ...  
19126                         None             None  
19127                         None             None  
19128                         None             None  
19129                         None             None  
19130                         None             None  

[19131 rows x 4 columns]

## Remove Duplicates

In [19]:
def remove_duplicates(df: pd.DataFrame) -> pd.DataFrame:

    return df.drop_duplicates(subset=None).drop_duplicates(["problem_abstract", "team"])

df = remove_duplicates(df)

## Split Data

In [20]:
from sklearn.model_selection import train_test_split

def train_valid_test_split(df: pd.DataFrame,
                           test_size : float,
                           valid_size : float,
                           random_state: int = 42,
                           shuffle : bool = True
                          ) -> Tuple[pd.DataFrame, pd.DataFrame, pd.DataFrame]:
    """Splits the dataset into train, validation and test dataframes and returns them in given order."""
    
    train_size = 1 - (test_size + valid_size)
    train_df, valid_and_test_df = train_test_split(df, train_size=train_size,
                                                   random_state=random_state, shuffle=shuffle)
    
    coeff = 1 / (test_size + valid_size)
    valid_df, test_df = train_test_split(valid_and_test_df, test_size=test_size * coeff,
                                         random_state=random_state, shuffle=shuffle)
    return train_df, valid_df, test_df

def split(df: pd.DataFrame) -> Tuple[pd.DataFrame, pd.DataFrame, pd.DataFrame, pd.DataFrame]:

    unlabeled = df[df["team"].apply(lambda s: s is None)]
    labeled = df.drop(unlabeled.index)
    train, valid, test = train_valid_test_split(labeled, 0.2, 0.2)
    return unlabeled, train, valid, test

unlabeled, train, valid, test = split(df)

## Save Data

In [ ]:
unlabeled.drop(columns=["hours_to_resolve", "team"]).to_csv(f"{OUT_DIR}/unlabeled.csv", index=False)
train.to_csv(f"{OUT_DIR}/train.csv", index=False)
valid.to_csv(f"{OUT_DIR}/valid.csv", index=False)
test.to_csv(f"{OUT_DIR}/test.csv", index=False)